In [19]:
import numpy as np
# bibiloteca para trabalhar com matrizes e arrays de forma eficiente 
import matplotlib.pyplot as plt
import collections
from bisect import insort
# biblioteca para listas encadeadas, filas e pilhas  
import time
import random
from math import log


In [20]:
grafo0 = r"C:\Users\Murilo\GRAFOS\grafo_0.txt"
grafo1 = r"C:\Users\Murilo\GRAFOS\grafo_1.txt"
grafo2 = r"C:\Users\Murilo\GRAFOS\grafo_2.txt"
grafo3 = r"C:\Users\Murilo\GRAFOS\grafo_3.txt"
grafo4 = r"C:\Users\Murilo\GRAFOS\grafo_4.txt"
grafo5 = r"C:\Users\Murilo\GRAFOS\grafo_5.txt"
grafo6 = r"C:\Users\Murilo\GRAFOS\grafo_6.txt"


In [21]:
class Graph:
     #inicializa um objeto do tipo grafo, necessita de um arquivo de input e o formato
     def __init__(self, ismatrix: bool, file: str): 
          self.ismatrix = ismatrix
          self.file = file
          with open(file) as f:
               self.n = int(f.readline())

     # carrega o grafo no formato desejado, já calcula a soma dos vértices e também o número de arestas
     def load(self):
          degreelist = []
          self.maxdegree = 0
          self.mindegree =  -1
          self.isloaded = True
          self.m = 0
          if self.ismatrix:

               self.matrix = np.full((self.n, self.n), False)

               with open(self.file) as f:
                    for edge in f:
                         try: 
                              edges = edge.split() 
                              if edges[0] != edges[1]:
                                   self.matrix[int(edges[0])-1][int(edges[1])-1] = True
                                   self.matrix[int(edges[1])-1][int(edges[0])-1] = True
                                   

                         
                         except: 
                              pass 
               self.m = int(np.sum(self.matrix)/2)
               
          else:
               self.array =  [collections.deque([]) for i in range(self.n)]
               with open(self.file) as f:
                    for edge in f:
                         try: 
                              edges = edge.split()
                              if ((int(edges[1]) not in self.array[int(edges[0])-1])) and (edges[0] != edges[1]) :   
                                   self.array[int(edges[0])-1].append(int(edges[1]))
                                   self.array[int(edges[1])-1].append(int(edges[0]))
                                   self.m+=1   
                         except: 
                              pass 

     def degrees(self):
          degreelist = []

          if self.ismatrix:
               for lin in self.matrix:
                    insort(degreelist, sum(lin))  
                    
          else:
               for index in self.array:
                    insort(degreelist, len(index))  
                         
          if self.n % 2 == 0:
              self.mediandegree = (degreelist[(self.n//2)-1]+degreelist[(self.n//2)])/2
          else:
               self.mediandegree = degreelist[(self.n//2)]   

          self.maxdegree  = degreelist[-1]
          self.mindegree = degreelist[0]

          self.averagedegree = self.m*2/self.n
          

          
     

     #retorna um vetor com os vizinhos de v                         
     def neighbours(self, v):
               neighbours = []

               if self.ismatrix:
                    for i in range(self.n):
                         if self.matrix[v-1][i]:
                              neighbours.append(i+1) 
                       
               else:
                    neighbours = list(self.array[v-1])     
               return neighbours
     
     
     def BFS(self, s):
          parents = [0 for i in range(self.n)]
          levels = [0 for i in range(self.n)]
          queue = collections.deque([])
          vector = [False for i in range(self.n)]
          vector[s-1] = True
          queue.insert(0,s)
          while len(queue) != 0:
               v = queue.pop()
               for w in self.neighbours(v):
                    if vector[w-1] == False:
                         vector[w-1] = True
                         parents[w-1] = v
                         levels[w-1] = levels[v-1] + 1
                         queue.insert(0,w)

          return {"parents" : parents, "levels" : levels, "visited": vector}
     

     def DFS(self, s):
          parents = [0 for i in range(self.n)]
          realparents = [0 for i in range(self.n)]
          reallevels = [0 for i in range(self.n)]
          levels = [0 for i in range(self.n)]
          pile = collections.deque([])
          vector = [False for i in range(self.n)]
          pile.append(s)
          while len(pile) != 0:
               u = pile.pop()
               if vector[u-1] == False:
                    vector[u-1] = True
                    realparents[u-1] = parents[u-1]
                    reallevels[u-1] = levels[u-1]
                    for v in self.neighbours(u):
                         parents[v-1] = u
                         levels[v-1] = levels[u-1]+1
                         pile.append(v)

          return {"parents" : realparents, "levels" : reallevels, "visited": vector}
     
     def dist_BFS(self,s, f):
          parents = [0 for i in range(self.n)]
          levels = [0 for i in range(self.n)]
          queue = collections.deque([])
          vector = [False for i in range(self.n)]
          vector[s-1] = True
          queue.insert(0,s)
          while len(queue) != 0:
               v = queue.pop()
               for w in self.neighbours(v):
                    if vector[w-1] == False:
                         vector[w-1] = True
                         parents[w-1] = v
                         levels[w-1] = levels[v-1] + 1
                         queue.insert(0,w)
               if vector[f-1] == True: break
          return levels[f-1]
     
     def aprox_diameter(self):
          diameter = 0
          for i in range(int(log(self.n)/log(2))):
               v = random.randint(1,self.n+1)
               distances = self.BFS(v)["levels"]
               max_distance = 0
               max_vertex = v
               for i in range(len(distances)):
                    if distances[i] > max_distance:
                         max_distance = distances[i]
                         max_vertex = i + 1
               max_distance2 = max(self.BFS(max_vertex)["levels"]) 
               if max_distance2 > diameter: diameter = max_distance2
          return diameter
     
     def real_diameter(self):
          real_diameter = 0
          for i in range(1, self.n+1):
               max_distance = max(self.BFS(i)["levels"]) 
               if max_distance > real_diameter: real_diameter = max_distance

          return real_diameter
     
     def lazy_diameter(self,v):
          distances = self.BFS(v)["levels"]
          max_distance = 0
          max_vertex = v
          for i in range(len(distances)):
               if distances[i] > max_distance:
                    max_distance = distances[i]
                    max_vertex = i + 1
          distances = self.BFS(max_vertex)["levels"]
          max_distance2 = max(self.BFS(max_vertex)["levels"]) 
          return max_distance2
     
     def lazy_aprox_diameter(self):
          max_diameter = 0
          for component in self.all_components:
               diameter_of_component = self.lazy_diameter(component[0])
               if diameter_of_component > max_diameter:
                    max_diameter = diameter_of_component
          return max_diameter


     
     def component(self, s):
          nodelist = []
          visited_nodes = self.BFS(s)["visited"]
          for i in range(len(visited_nodes)):
               if visited_nodes[i]:
                    nodelist.append(i+1)
          return {"nodelist": nodelist, "visitedlist": visited_nodes}

       
     
     def load_all_components(self):
          components = []
          seen = [False for i in range(self.n)]
          for i in range(len(seen)):
               if seen[i] == False:
                    component = self.component(i+1)
                    components.append(component["nodelist"])
                    for i in range(len(seen)):
                         if seen[i] == False: 
                              if component["visitedlist"][i]:
                                   seen[i] = True
          self.all_components = components                        
             






In [5]:
def degree_info(graph: Graph):
    graph.degrees()
    print(f"Vértices: {graph.n}, Arestas: {graph.m}, Grau máximo: {graph.maxdegree}, Grau mínimo: {graph.mindegree}, Grau médio: {graph.averagedegree}, mediana do Grau: {graph.mediandegree}")

In [6]:
def real_component_info(graph: Graph):
    componentlist = graph.all_components
    components_number = len(componentlist)
    componentlist.sort(key=len)
    print(f"Diametro do grafo: {graph.real_diameter()}")
    print(f"Número de componentes conéxas: {components_number}, Componentes em ordem crescente de tamanho:")
    for component in componentlist:
        print("tamanho:", end=" ")
        print(len(component), end=" ")
        print("lista:", end=" ")
        print(component)
   
    

In [22]:
def aprox_component_info(graph: Graph):
    componentlist = graph.all_components
    components_number = len(componentlist)
    componentlist.sort(key=len)
    print(f"Diametro do grafo: {graph.lazy_aprox_diameter()}")
    print(f"Número de componentes conéxas: {components_number}, Componentes em ordem crescente de tamanho:")
    for component in componentlist:
        print("tamanho:", end=" ")
        print(len(component), end=" ")
        print("lista:", end=" ")
        print(component)

In [23]:
def real_info(graph):
    degree_info(graph)
    real_component_info(graph)


In [24]:
def aprox_info(graph):
    degree_info(graph)
    aprox_component_info(graph)

In [32]:
graph1_array = Graph(False, grafo1)  
graph1_array.load()
graph1_array.load_all_components()

In [11]:
aprox_info(graph1_array)

Vértices: 10000, Arestas: 109921, Grau máximo: 43, Grau mínimo: 8, Grau médio: 21.9842, mediana do Grau: 22.0
Diametro do grafo: 4
Número de componentes conéxas: 1, Componentes em ordem crescente de tamanho:
tamanho: 10000 lista: [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 17

In [12]:
graph2_array = Graph(False, grafo2)  
graph2_array.load()
graph2_array.load_all_components()

In [14]:
aprox_info(graph2_array)

Vértices: 49948, Arestas: 1298710, Grau máximo: 112, Grau mínimo: 1, Grau médio: 52.00248258188516, mediana do Grau: 55.0
Diametro do grafo: 20
Número de componentes conéxas: 10, Componentes em ordem crescente de tamanho:
tamanho: 48 lista: [764, 1877, 2380, 3411, 4201, 5792, 7981, 8413, 9944, 10047, 11425, 12829, 16646, 16756, 17340, 18880, 19733, 19831, 20455, 21837, 24534, 26291, 27166, 27196, 27420, 27550, 29299, 31143, 33066, 33362, 35620, 37053, 37301, 37465, 38767, 39513, 39688, 41183, 42053, 42088, 43256, 43448, 44128, 44722, 45055, 45774, 46507, 47782]
tamanho: 97 lista: [376, 1088, 1156, 1462, 1580, 2505, 2514, 2793, 3595, 4789, 5186, 6589, 8195, 8369, 8500, 8516, 9027, 10136, 11635, 11661, 11814, 12612, 12985, 14322, 14404, 14579, 15010, 15966, 16874, 16962, 17402, 17474, 18660, 18716, 19052, 20211, 20698, 21313, 21434, 21696, 22294, 22699, 22974, 23177, 23888, 24589, 24997, 26772, 27137, 28033, 28310, 28337, 28527, 29896, 30922, 31175, 31262, 31424, 31448, 31693, 31859, 328

In [15]:
graph3_array = Graph(False, grafo3)  
graph3_array.load()
graph3_array.load_all_components()

In [16]:
aprox_info(graph3_array)

Vértices: 375000, Arestas: 765615, Grau máximo: 15, Grau mínimo: 1, Grau médio: 4.08328, mediana do Grau: 4.0
Diametro do grafo: 22
Número de componentes conéxas: 2, Componentes em ordem crescente de tamanho:
tamanho: 125000 lista: [1, 7, 11, 17, 19, 21, 23, 27, 30, 35, 39, 40, 43, 45, 46, 47, 50, 51, 54, 55, 57, 63, 64, 68, 70, 75, 79, 83, 84, 89, 90, 93, 97, 99, 105, 108, 112, 118, 120, 121, 123, 129, 130, 131, 132, 135, 143, 145, 146, 155, 158, 159, 160, 161, 163, 185, 186, 187, 189, 190, 191, 192, 200, 203, 204, 206, 208, 217, 221, 227, 228, 231, 233, 234, 243, 249, 250, 255, 260, 264, 268, 273, 278, 280, 281, 282, 296, 297, 300, 302, 306, 308, 311, 316, 317, 318, 323, 326, 328, 330, 331, 333, 339, 342, 343, 346, 347, 351, 352, 359, 361, 372, 375, 378, 381, 386, 388, 390, 392, 398, 399, 400, 401, 410, 416, 417, 422, 424, 430, 435, 438, 439, 440, 441, 442, 444, 447, 451, 456, 457, 458, 462, 464, 466, 472, 474, 478, 482, 484, 485, 490, 495, 498, 502, 505, 506, 507, 508, 513, 517, 519

In [17]:
graph4_array = Graph(False, grafo4)  
graph4_array.load()
graph4_array.load_all_components()

In [18]:
aprox_info(graph4_array)

Vértices: 375000, Arestas: 8186986, Grau máximo: 89, Grau mínimo: 9, Grau médio: 43.66392533333333, mediana do Grau: 47.0
Diametro do grafo: 5
Número de componentes conéxas: 2, Componentes em ordem crescente de tamanho:
tamanho: 125000 lista: [2, 3, 4, 7, 9, 12, 15, 16, 18, 24, 27, 29, 31, 35, 39, 40, 42, 47, 48, 49, 51, 53, 59, 61, 62, 70, 73, 74, 76, 84, 85, 86, 91, 94, 98, 99, 101, 103, 106, 109, 110, 111, 112, 117, 118, 119, 120, 124, 128, 129, 137, 140, 143, 145, 152, 153, 156, 158, 160, 166, 169, 170, 171, 172, 173, 176, 179, 181, 191, 194, 209, 213, 215, 216, 218, 219, 220, 225, 226, 227, 238, 241, 242, 244, 245, 246, 248, 249, 252, 260, 261, 269, 270, 273, 274, 276, 278, 279, 280, 281, 282, 284, 291, 299, 303, 306, 307, 310, 317, 322, 323, 324, 325, 326, 327, 331, 333, 338, 339, 341, 344, 345, 347, 349, 353, 355, 356, 357, 358, 360, 361, 367, 372, 373, 376, 381, 383, 388, 389, 392, 393, 396, 397, 399, 401, 402, 404, 408, 409, 412, 415, 417, 422, 426, 430, 435, 438, 452, 456, 46

In [ ]:
graph5_array = Graph(False, grafo5)  
graph5_array.load()
graph5_array.load_all_components()
gc.collect

In [ ]:
aprox_info(graph5_array)

In [ ]:
graph6_array = Graph(False, grafo6)  
graph6_array.load()
graph6_array.load_all_components()

In [ ]:
aprox_info(graph6_array)